# 本番環境でのAutoGenエージェント: 可観測性と評価

このチュートリアルでは、[Autogenエージェント](https://github.com/microsoft/autogen)の**内部ステップ（トレース）を監視**し、[Langfuse](https://langfuse.com)を使用して**パフォーマンスを評価**する方法を学びます。

このガイドでは、エージェントを迅速かつ信頼性高く本番環境に導入するために使用される**オンライン**および**オフライン**評価指標について説明します。

**AIエージェントの評価が重要な理由:**
- タスクが失敗したり、最適でない結果を出した場合の問題のデバッグ
- コストとパフォーマンスをリアルタイムで監視
- 継続的なフィードバックを通じて信頼性と安全性を向上


## ステップ 1: 環境変数を設定する

[Langfuse Cloud](https://cloud.langfuse.com/)に登録するか、[Langfuseをセルフホスト](https://langfuse.com/self-hosting)して、Langfuse APIキーを取得してください。

_**注:** セルフホスト利用者は、[Terraformモジュール](https://langfuse.com/self-hosting/azure)を使用してAzure上にLangfuseをデプロイすることができます。または、[Helmチャート](https://langfuse.com/self-hosting/kubernetes-helm)を使用してKubernetes上にLangfuseをデプロイすることも可能です。_


In [5]:
import os

# Get keys for your project from the project settings page: https://cloud.langfuse.com
os.environ["LANGFUSE_PUBLIC_KEY"] = "pk-lf-..." 
os.environ["LANGFUSE_SECRET_KEY"] = "sk-lf-..." 
os.environ["LANGFUSE_HOST"] = "https://cloud.langfuse.com" # 🇪🇺 EU region
# os.environ["LANGFUSE_HOST"] = "https://us.cloud.langfuse.com" # 🇺🇸 US region

環境変数が設定されたら、Langfuseクライアントを初期化することができます。`get_client()`は、環境変数で提供された認証情報を使用してLangfuseクライアントを初期化します。


In [6]:
from langfuse import Langfuse
 
# Filter out Autogen OpenTelemetryspans
langfuse = Langfuse(
    blocked_instrumentation_scopes=["autogen SingleThreadedAgentRuntime"]
)
 
# Verify connection
if langfuse.auth_check():
    print("Langfuse client is authenticated and ready!")
else:
    print("Authentication failed. Please check your credentials and host.")

Langfuse client is authenticated and ready!


## ステップ 2: OpenLit インストゥルメンテーションの初期化

次に、[OpenLit](https://github.com/openlit/openlit) のインストゥルメンテーションを初期化します。OpenLit は自動的に AutoGen の操作をキャプチャし、OpenTelemetry (OTel) のスパンを Langfuse にエクスポートします。


In [7]:
import openlit
 
# Initialize OpenLIT instrumentation. The disable_batch flag is set to true to process traces immediately.
openlit.init(tracer=langfuse._otel_tracer, disable_batch=True, disabled_instrumentors=["mistral"])

## ステップ 3: エージェントを実行する

次に、インストルメンテーションをテストするためのマルチターンエージェントを設定します。


In [2]:
import os

from autogen_agentchat.agents import AssistantAgent
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_agentchat.base import TaskResult

from autogen_agentchat.conditions import TextMentionTermination
from autogen_agentchat.teams import RoundRobinGroupChat

In [3]:
client = AzureAIChatCompletionClient(
    model="gpt-4o-mini",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.environ["GITHUB_TOKEN"]),
    model_info={
        "json_output": True,
        "function_calling": True,
        "vision": True,
        "family": "unknown",
        "structured_output": False
    },
)

In [8]:
# 🍴 Agent 1 – proposes ONE healthy meal idea each turn
meal_planner_agent = AssistantAgent(
    "meal_planner_agent",
    model_client=client,
    description="A seasoned meal-planning coach who suggests balanced meals.",
    system_message="""
    You are a Meal-Planning Assistant with a decade of experience helping busy people prepare meals.
    Goal: propose the single best meal (breakfast, lunch, or dinner) given the user's context.
    Each response must contain ONLY one complete meal idea (title + very brief component list) — no extras.
    Keep it concise: skip greetings, chit-chat, and filler.
    """,
)

# 🥗 Agent 2 – checks nutritional quality & variety
nutritionist_agent = AssistantAgent(
    "nutritionist_agent",
    model_client=client,
    description="A registered dietitian ensuring meals meet nutritional standards.",
    system_message="""
    You are a Nutritionist focused on whole-food, macro-balanced eating.
    Evaluate the meal_planner_agent’s recommendation.
    If the meal is nutritionally sound, sufficiently varied, and portion-appropriate, respond with 'APPROVE'.
    Otherwise, give high-level guidance on how to improve it (e.g. 'add a plant-based protein') — do NOT provide a full alternative recipe.
    """,
)

In [9]:
# ✅ Chat stops once the nutritionist says APPROVE
termination = TextMentionTermination("APPROVE")

# 🔄 Alternate turns between the two agents until termination
team = RoundRobinGroupChat(
    [meal_planner_agent, nutritionist_agent],
    termination_condition=termination,
)

# Example kickoff
user_input = "I'm looking for a quick, delicious dinner I can prep after work. I have 30 minutes and minimal clean-up is ideal."

In [ ]:
with langfuse.start_as_current_span(name="create_meal_plan") as span:
    async for message in team.run_stream(task=user_input):
        if isinstance(message, TaskResult):
            print("Stop Reason:", message.stop_reason)
        else:
            print(message)

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

# Flush the trace to Langfuse for short-lived environments such as Jupyter Notebooks
langfuse.flush()

### トレース構造

Langfuseは、**トレース**を記録し、その中にエージェントのロジックの各ステップを表す**スパン**を含みます。この例では、トレースにはエージェント全体の実行と以下のサブスパンが含まれています：
- 食事プランナーエージェント
- 栄養士エージェント

これらを調査することで、時間がどこで使われているか、使用されたトークンの数などを正確に確認することができます。

![Langfuseのトレースツリー](https://langfuse.com/images/cookbook/example-autogen-evaluation/trace-tree.png)

_[トレースへのリンク](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


## オンライン評価

オンライン評価とは、エージェントを実際の運用環境、つまり本番での使用中に評価することを指します。これには、エージェントが実際のユーザーとのやり取りでどのように機能しているかを監視し、結果を継続的に分析することが含まれます。

### 本番環境で追跡すべき一般的な指標

1. **コスト** — 計測ツールがトークン使用量を記録し、トークンごとの価格を割り当てることで概算コストに変換できます。
2. **レイテンシー** — 各ステップや全体の実行にかかる時間を観察します。
3. **ユーザーフィードバック** — ユーザーは直接フィードバック（良い/悪い）を提供することで、エージェントの改善や修正を支援できます。
4. **LLMをジャッジとして使用** — 別のLLMを使用して、エージェントの出力をほぼリアルタイムで評価します（例: 有害性や正確性のチェック）。

以下に、これらの指標の例を示します。


#### 1. コスト

以下は、`gpt-4o-mini` 呼び出しの使用状況を示すスクリーンショットです。これにより、コストのかかるステップを確認し、エージェントを最適化するのに役立ちます。

![Costs](https://langfuse.com/images/cookbook/example-autogen-evaluation/gpt-4o-costs.png) 

_[トレースへのリンク](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64)_


#### 2. レイテンシー

各ステップを完了するのにどれくらい時間がかかったかも確認できます。以下の例では、全体の実行に約3秒かかっており、それをステップごとに分解して見ることができます。これにより、ボトルネックを特定し、エージェントを最適化するのに役立ちます。

![レイテンシー](https://langfuse.com/images/cookbook/example-autogen-evaluation/agent-latency.png) 

_[トレースへのリンク](https://cloud.langfuse.com/project/cloramnkj0002jz088vzn1ja4/traces/dac2b33e7cd709e685ccf86a137ecc64?display=timeline)_


#### 3. ユーザーフィードバック

エージェントがユーザーインターフェースに組み込まれている場合、チャットUIでの「いいね」や「悪いね」のような直接的なユーザーフィードバックを記録することができます。


In [10]:
from langfuse import get_client
 
langfuse = get_client()
 
# Option 1: Use the yielded span object from the context manager
with langfuse.start_as_current_span(
    name="autogen-request-user-feedback-1") as span:
    
    async for message in team.run_stream(task="Create a meal with potatoes"):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using the span object
    span.score_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC",
        comment="This was delicious, thank you"
    )
 
# Option 2: Use langfuse.score_current_trace() if still in context
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:
    # ... Autogen execution ...

    async for message in team.run_stream(task="I am allergic to gluten."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message)    
 
    # Score using current context
    langfuse.score_current_trace(
        name="user-feedback",
        value=1,
        data_type="NUMERIC"
    )

id='da068880-22ae-4f01-9f01-2bb231939089' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 43, 732669, tzinfo=datetime.timezone.utc) content='Create a meal with potatoes' type='TextMessage'
id='ad937ce4-3534-493f-824b-ca9c226b5287' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=95, completion_tokens=30) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 186423, tzinfo=datetime.timezone.utc) content='Potato and Spinach Frittata  \n- Eggs  \n- Potatoes  \n- Fresh spinach  \n- Onion  \n- Cheese (optional)  ' type='TextMessage'
id='50fd33c1-057f-49fe-afad-ee86d164296d' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=132, completion_tokens=4) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 20, 45, 581059, tzinfo=datetime.timezone.utc) content='APPROVE' type='TextMessage'
Stop Reason: Text 'APPROVE' mentioned
id='e371de6c-e5fc-42c1-8eda-e5b8cd5accab' source='user' models_usage=None met

In [ ]:
# Option 3: Use create_score() with trace ID (when outside context)
langfuse.create_score(
    trace_id="predefined_trace_id",
    name="user-feedback",
    value=1,
    data_type="NUMERIC",
    comment="This was correct, thank you"
)

ユーザーのフィードバックはその後、Langfuseで記録されます:

![ユーザーのフィードバックはLangfuseで記録されています](https://langfuse.com/images/cookbook/example-autogen-evaluation/user-feedback.png)


#### 4. 自動化されたLLM-as-a-Judgeスコアリング

LLM-as-a-Judgeは、エージェントの出力を自動的に評価するもう一つの方法です。別のLLMを使用して、出力の正確性、有害性、スタイル、またはその他の重要な基準を評価する仕組みを設定できます。

**ワークフロー**:
1. **評価テンプレート**を定義します。例: 「テキストが有害かどうかを確認する。」
2. 判定用モデルを設定します。この場合、Azure経由でクエリされる`gpt-4o-mini`を使用します。
3. エージェントが出力を生成するたびに、その出力をテンプレートとともに「判定」LLMに渡します。
4. 判定LLMが評価やラベルを返答し、それを観測ツールに記録します。

Langfuseの例:

![LLM-as-a-Judge Evaluator](https://langfuse.com/images/cookbook/example-autogen-evaluation/evaluator.png)


In [12]:
with langfuse.start_as_current_span(name="autogen-request-user-feedback-2") as span:

    async for message in team.run_stream(task="I am a picky eater and not sure if you find something for me."):
            if isinstance(message, TaskResult):
                print("Stop Reason:", message.stop_reason)
            else:
                print(message) 

    span.update_trace(
        input=user_input,
        output=message.stop_reason,
    )

langfuse.flush()

id='eefc628d-502f-451a-8f70-be486f62f8c5' source='user' models_usage=None metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 29, 171393, tzinfo=datetime.timezone.utc) content='I am a picky eater and not sure if you find something for me.' type='TextMessage'
id='13b3e14b-bcf7-42a5-80d6-54b0c7be765e' source='meal_planner_agent' models_usage=RequestUsage(prompt_tokens=352, completion_tokens=27) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 30, 433516, tzinfo=datetime.timezone.utc) content='Chicken Alfredo Pasta  \n- Gluten-free pasta  \n- Grilled chicken breast  \n- Heavy cream  \n- Parmesan cheese  \n- Garlic  ' type='TextMessage'
id='550f2dee-0e08-4bbd-b67f-991b467328f1' source='nutritionist_agent' models_usage=RequestUsage(prompt_tokens=386, completion_tokens=17) metadata={} created_at=datetime.datetime(2025, 7, 2, 16, 38, 31, 505173, tzinfo=datetime.timezone.utc) content='Consider incorporating some vegetables, like spinach or broccoli, to increase the nutrien

この例の回答は「有害ではない」と判断されています。

![LLM-as-a-Judge 評価スコア](https://langfuse.com/images/cookbook/example-autogen-evaluation/llm-as-a-judge-score.png)


#### 5. 可観測性メトリクスの概要

これらすべてのメトリクスはダッシュボードで一緒に視覚化することができます。これにより、エージェントが多くのセッションでどのように動作しているかを素早く確認でき、時間の経過とともに品質メトリクスを追跡するのに役立ちます。

![可観測性メトリクスの概要](https://langfuse.com/images/cookbook/example-autogen-evaluation/dashboard.png)


## オフライン評価

オンライン評価はリアルタイムのフィードバックに欠かせませんが、**オフライン評価**も必要です。これは、開発前や開発中に体系的なチェックを行うことで、変更を本番環境に反映する前に品質と信頼性を維持するのに役立ちます。


### データセット評価

オフライン評価では、通常以下の手順を行います：
1. ベンチマークデータセット（プロンプトと期待される出力のペアを含む）を用意する
2. そのデータセットでエージェントを実行する
3. 出力を期待される結果と比較する、または追加のスコアリング手法を使用する

以下では、質問と期待される回答を含む [q&a-dataset](https://huggingface.co/datasets/junzhang1207/search-dataset) を使ったこのアプローチを示します。


In [16]:
import pandas as pd
from datasets import load_dataset
 
# Fetch search-dataset from Hugging Face
dataset = load_dataset("junzhang1207/search-dataset", split = "train")
df = pd.DataFrame(dataset)
print("First few rows of search-dataset:")
print(df.head())

/Users/jannik/Documents/GitHub/ai-agents-for-beginners/.venv/lib/python3.13/site-packages/tqdm/auto.py:21: TqdmWarning: IProgress not found. Please update jupyter and ipywidgets. See https://ipywidgets.readthedocs.io/en/stable/user_install.html
  from .autonotebook import tqdm as notebook_tqdm


First few rows of search-dataset:
                                     id  \
0  20caf138-0c81-4ef9-be60-fe919e0d68d4   
1  1f37d9fd-1bcc-4f79-b004-bc0e1e944033   
2  76173a7f-d645-4e3e-8e0d-cca139e00ebe   
3  5f5ef4ca-91fe-4610-a8a9-e15b12e3c803   
4  64dbed0d-d91b-4acd-9a9c-0a7aa83115ec   

                                            question  \
0                 steve jobs statue location budapst   
1  Why is the Battle of Stalingrad considered a t...   
2  In what year did 'The Birth of a Nation' surpa...   
3  How many Russian soldiers surrendered to AFU i...   
4   What event led to the creation of Google Images?   

                                     expected_answer       category       area  
0  The Steve Jobs statue is located in Budapest, ...           Arts  Knowledge  
1  The Battle of Stalingrad is considered a turni...   General News       News  
2  This question is based on a false premise. 'Th...  Entertainment       News  
3  About 300 Russian soldiers surrendered to t

次に、Langfuseでデータセットエンティティを作成して実行を追跡します。その後、データセットの各項目をシステムに追加します。


In [17]:
from langfuse import Langfuse
langfuse = Langfuse()
 
langfuse_dataset_name = "qa-dataset_autogen-agent"
 
# Create a dataset in Langfuse
langfuse.create_dataset(
    name=langfuse_dataset_name,
    description="q&a dataset uploaded from Hugging Face",
    metadata={
        "date": "2025-03-21",
        "type": "benchmark"
    }
)

Dataset(id='cmcm7524d00kjad07s2cjwqcf', name='qa-dataset_autogen-agent', description='q&a dataset uploaded from Hugging Face', metadata={'date': '2025-03-21', 'type': 'benchmark'}, project_id='cloramnkj0002jz088vzn1ja4', created_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc), updated_at=datetime.datetime(2025, 7, 2, 16, 54, 7, 357000, tzinfo=datetime.timezone.utc))

In [18]:
df_25 = df.sample(25) # For this example, we upload only 25 dataset questions

for idx, row in df_25.iterrows():
    langfuse.create_dataset_item(
        dataset_name=langfuse_dataset_name,
        input={"text": row["question"]},
        expected_output={"text": row["expected_answer"]}
    )

![データセット項目のLangfuse](https://langfuse.com/images/cookbook/example-autogen-evaluation/example-dataset.png)


#### データセットでエージェントを実行する

まず、Azure OpenAIモデルを使用して質問に答えるシンプルなAutogenエージェントを組み立てます。


In [8]:
import os
from dotenv import load_dotenv

from autogen_agentchat.agents import AssistantAgent
from autogen_core.models import UserMessage
from autogen_ext.models.azure import AzureAIChatCompletionClient
from azure.core.credentials import AzureKeyCredential
from autogen_core import CancellationToken
from autogen_agentchat.messages import TextMessage

In [ ]:
load_dotenv()
client = AzureAIChatCompletionClient(
    model="gpt-4o",
    endpoint="https://models.inference.ai.azure.com",
    # To authenticate with the model you will need to generate a personal access token (PAT) in your GitHub settings.
    # Create your PAT token by following instructions here: https://docs.github.com/en/authentication/keeping-your-account-and-data-secure/managing-your-personal-access-tokens
    credential=AzureKeyCredential(os.getenv("GITHUB_TOKEN")),
    max_tokens=5000,
    model_info={
        "json_output": True,
        "function_calling": False,
        "vision": False,
        "family": "unknown",
        "structured_output": True,
    },
)

result = await client.create([UserMessage(content="What is the capital of France?", source="user")])
print(result)

In [18]:
agent = AssistantAgent(
    name="assistant",
    model_client=client,
    tools=[],
    system_message="You are participant in a quizz show and you are given a question. You need to create a short answer to the question.",
)

次に、補助関数 `my_agent()` を定義します。


In [19]:
async def my_agent(user_query: str):

    with langfuse.start_as_current_span(name="autogen-trace") as span:

        # Execute the agent response
        response = await agent.on_messages(
            [TextMessage(content=user_query, source="user")],
            cancellation_token=CancellationToken(),
        )

        span.update_trace(
            input=user_query,
            output=response.chat_message.content,
        )

    return str(response.chat_message.content)

# Test the function
await my_agent("What is the capital of France?")

'The capital of France is Paris.'

最後に、各データセット項目をループし、エージェントを実行して、トレースをデータセット項目にリンクします。必要に応じて簡易評価スコアを添付することもできます。


In [20]:
dataset_name = "qa-dataset_autogen-agent"
current_run_name = "dev_tasks_run-autogen_gpt-4.1" # Identifies this specific evaluation run
current_run_metadata={"model_provider": "Azure", "model": "gpt-4.1"}
current_run_description="Evaluation run for Autogen model on July 3rd"

dataset = langfuse.get_dataset('qa-dataset_autogen-agent')

for item in dataset.items:
    print(f"Running evaluation for item: {item.id} (Input: {item.input})")
 
    # Use the item.run() context manager
    with item.run(
        run_name=current_run_name,
        run_metadata=current_run_metadata,
        run_description=current_run_description
    ) as root_span: 
        # All subsequent langfuse operations within this block are part of this trace.
        generated_answer = await my_agent(user_query = item.input["text"])
    
    print("Generated Answer: ", generated_answer)
 
print(f"\nFinished processing dataset '{dataset_name}' for run '{current_run_name}'.")

langfuse.flush()

Running evaluation for item: 09810cc4-9992-4712-a3b2-7224da31776a (Input: {'text': 'In Hindu mythology, which deity is the Ganges river dolphin associated with?'})
Generated Answer:  In Hindu mythology, the Ganges river dolphin is associated with the deity Ganga.
Running evaluation for item: bb113f94-7723-47c6-8c34-59d883044514 (Input: {'text': 'What significant discovery did the LHCb collaboration report in 2015?'})
Generated Answer:  In 2015, the LHCb collaboration reported the discovery of pentaquark particles.
Running evaluation for item: 4d8ae54e-ceab-46d0-ad2c-6e8e223589a9 (Input: {'text': 'What is the MÄ\x81ori name for the red-crowned parakeet?'})
Generated Answer:  The Māori name for the red-crowned parakeet is kākāriki.
Running evaluation for item: 21e5a0d5-f619-4a73-868e-9955053b3e72 (Input: {'text': 'Who starred in the 1978 television film adaptation of Les MisÃ©rables?'})
Generated Answer:  Richard Jordan starred as Jean Valjean in the 1978 television film adaptation of Le

異なるエージェント構成でこのプロセスを繰り返すことができます。例えば：

- モデル (gpt-4o-mini, gpt-4.1 など)
- プロンプト
- ツール (検索あり vs 検索なし)
- エージェントの複雑さ (マルチエージェント vs シングルエージェント)

その後、Langfuseでそれらを並べて比較します。この例では、25のデータセット質問に対してエージェントを3回実行しました。各実行では異なるAzure OpenAIモデルを使用しました。より大きなモデルを使用すると、正しく回答された質問の数が増加することが確認できます (予想通り)。`correct_answer` スコアは、データセット内のサンプル回答に基づいて質問の正確性を判断するよう設定された [LLM-as-a-Judge Evaluator](https://langfuse.com/docs/scores/model-based-evals) によって作成されます。

![データセット実行概要](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset_runs.png)
![データセット実行比較](https://langfuse.com/images/cookbook/example-autogen-evaluation/dataset-run-comparison.png)



---

**免責事項**:  
この文書は、AI翻訳サービス [Co-op Translator](https://github.com/Azure/co-op-translator) を使用して翻訳されています。正確性を追求しておりますが、自動翻訳には誤りや不正確な部分が含まれる可能性があることをご承知ください。元の言語で記載された文書が正式な情報源とみなされるべきです。重要な情報については、専門の人間による翻訳を推奨します。この翻訳の使用に起因する誤解や誤解釈について、当方は責任を負いません。
